# Building databases of published works  

> Pragmatic tools for constructing databases of scientific works based on queries defined with Boolean Logic.

In [5]:
#| default_exp utils.db

In [6]:
#| hide
from nbdev import *

In [1]:
#| export

import local_resources.linkml as linkml

from alhazen.utils.airtableUtils import AirtableUtils
from alhazen.utils.searchEngineUtils import ESearchQuery, EuroPMCQuery
from alhazen.utils.queryTranslator import QueryTranslator, QueryType
from alhazen.schema_sqla import ScientificKnowledgeCollection, ScientificKnowledgeExpression, \
    ScientificKnowledgeFragment, Note
from alhazen.schema_sqla import ScientificKnowledgeCollection, \
    ScientificKnowledgeExpression, ScientificKnowledgeCollectionHasMembers, \
    ScientificKnowledgeItem, ScientificKnowledgeExpressionHasRepresentation, \
    ScientificKnowledgeFragment, ScientificKnowledgeItemHasPart, \
    InformationResource

import alhazen.schema_python as linkml_py
from alhazen.utils.jats_text_extractor import NxmlDoc
from alhazen.utils.local_literature_db import *

from bs4 import BeautifulSoup,Tag,Comment,NavigableString
from databricks import sql
from datetime import datetime
from importlib_resources import files
import os
import pandas as pd
from pathlib import Path
import re
import requests
from sqlalchemy import create_engine, exists
from sqlalchemy.orm import sessionmaker
from time import time,sleep
from tqdm import tqdm
from urllib.request import urlopen
from urllib.parse import quote_plus, quote, unquote
from urllib.error import URLError, HTTPError

In [2]:
db = LocalLiteratureDb('/Users/gburns/alhazen/', 'em_tech' )
if db.session is None:
    session_class = sessionmaker(bind=db.engine)
    db.session = session_class()

In [3]:
from io import StringIO

EM_QUERIES_TSV = '''
ID,NAME,QUERY
0,Hierarchical phase-contrast tomography,Hierarchical phase-contrast tomography | HIP-CT | Hierarchical phase contrast tomography
1,Cryo-Electron Tomography,Cryoelectron Tomography | Cryo Electron Tomography | Cryo-Electron Tomography | Cryo-ET | CryoET
2,Volume Electron Microscopy,Volume Electron Microscopy | Volume EM | (serial section & (electron microscopy | EM | transmission electron microscopy | TEM | scanning electron microscopy | SEM | electron tomography )) | (serial block-face & (SEM | scanning electron microscopy)) | (focused ion beam & (SEM | scanning electron microscopy)) | (automated serial & (TEM | transmission electron microscopy)) | ( massively parallel imaging & (SEM | scanning electron microscopy)) | multibeam SEM | FAST-SEM | cryo-TEM
'''
EM_QUERIES_TSV = '''
ID,NAME,QUERY
0,Cryo-Electron Tomography,Cryoelectron Tomography | Cryo Electron Tomography | Cryo-Electron Tomography | Cryo-ET | CryoET
'''

cdf = pd.read_csv(StringIO(EM_QUERIES_TSV), sep=',')
qs = QuerySpec('EM Technology', 'ID', 'QUERY', 'NAME', {}, ['TITLE','ABSTRACT', 'METHODS'])
qt = QueryTranslator(cdf.sort_values('ID'), 'ID', 'QUERY', 'NAME')

db.add_corpus_from_epmc(qt, None, sections=qs.sections)


100%|██████████| 1/1 [00:00<00:00, 1057.30it/s]


100%|██████████| 1/1 [00:00<00:00, 1061.58it/s]


https://www.ebi.ac.uk/europepmc/webservices/rest/search?format=JSON&pageSize=1000&synonym=TRUE&resultType=core&query=((TITLE:"Cryoelectron Tomography" OR ABSTRACT:"Cryoelectron Tomography" OR METHODS:"Cryoelectron Tomography") OR (TITLE:"Cryo Electron Tomography" OR ABSTRACT:"Cryo Electron Tomography" OR METHODS:"Cryo Electron Tomography") OR (TITLE:"Cryo-Electron Tomography" OR ABSTRACT:"Cryo-Electron Tomography" OR METHODS:"Cryo-Electron Tomography") OR (TITLE:"Cryo-ET" OR ABSTRACT:"Cryo-ET" OR METHODS:"Cryo-ET") OR (TITLE:"CryoET" OR ABSTRACT:"CryoET" OR METHODS:"CryoET")), 2463 European PMC PAPERS FOUND


100%|██████████| 3/3 [00:37<00:00, 12.66s/it]


 Returning 2463


  0%|          | 0/2463 [00:00<?, ?it/s]/Users/gburns/Documents/Coding/ChatGPT_etc/alzhazen/alhazen/utils/local_literature_db.py:370: SAWarning: SELECT statement has a cartesian product between FROM element(s) "ScientificKnowledgeExpression" and FROM element "ScientificKnowledgeCollection".  Apply join condition(s) between each element to resolve.
  .filter(ScientificKnowledgeCollection.id==p_id).first()
100%|██████████| 2463/2463 [00:03<00:00, 712.98it/s]


In [20]:
db.session.rollback()

In [4]:
db.session.commit()

In [12]:
os.environ['NCBI_API_KEY'] = 'd086451c882fabace54d7b049b6fb8481908'
db.add_full_text_for_collection(0)

https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2023.07.17.549278[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2023.09.05.556310[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2023.10.10.561643[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1016/j.coviro.2023.101338[doi]&retmode=xml
No paper found with that DOI


rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)


https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1002/1873-3468.14726[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2023.11.10.566563[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1109/tvcg.2022.3186146[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2023.10.05.560879[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1038/s41592-023-02045-0[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?ap

AttributeError: 'NoneType' object has no attribute 'TOP_SECTION'

In [6]:
db.session.commit()

In [6]:
db.session.rollback()

In [6]:
q = db.session.query(ScientificKnowledgeExpression) \
                .filter(ScientificKnowledgeExpression.content.like('%Jensen%')) 

os.environ['NCBI_API_KEY'] = 'd086451c882fabace54d7b049b6fb8481908'

l = []
for e in q.all():
    l.append({'id':e.id, 
              'xrefs':e.xref,
              'name':e.name, 
              'citation':e.content, 
              'items':'|'.join([i.type for i in e.has_representation])})
    try: 
        db.add_full_text_for_expression(e)
        db.session.commit()
    except Exception as ex:
        print(ex)
        db.session.rollback()
        sleep(1)
        continue
df = pd.DataFrame(l)
df

'NoneType' object has no attribute 'TOP_SECTION'
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1038/s41564-023-01401-2[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2023.07.04.547645[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2022.08.23.505044[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2022.02.17.480955[doi]&retmode=xml
No paper found with that DOI
'NoneType' object has no attribute 'TOP_SECTION'
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2022.06.21.496981[doi]&re

rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)
rewritetex: likely error invoking catdvi (empty output)


https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2022.01.31.478342[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2022.06.13.496000[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1016/j.bpj.2023.07.030[doi]&retmode=xml
No paper found with that DOI
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2021.07.06.451241[doi]&retmode=xml
No paper found with that DOI
'NoneType' object has no attribute 'TOP_SECTION'
https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esearch.fcgi?api_key=d086451c882fabace54d7b049b6fb8481908&db=pmc&term=10.1101/2021.11.02.466666[doi]&retmode=xml
No paper found with that DOI
https://eut

id                                              xrefs  name  \
0    epmid:37176000         [doi:10.3390/ijms24098292, epmid:37176000]  None   
1    epmid:36561119      [doi:10.21769/bioprotoc.4559, epmid:36561119]  None   
2    epmid:37349588   [doi:10.1038/s41564-023-01401-2, epmid:37349588]  None   
3    epmid:37485371   [doi:10.1016/j.isci.2023.107210, epmid:37485371]  None   
4   epmid:PPR686654   [doi:10.1101/2023.07.04.547645, epmid:PPR686654]  None   
5    epmid:33771860       [doi:10.1126/sciadv.abc6345, epmid:33771860]  None   
6    epmid:35508170    [doi:10.1016/j.cub.2022.04.024, epmid:35508170]  None   
7   epmid:PPR535975   [doi:10.1101/2022.08.23.505044, epmid:PPR535975]  None   
8   epmid:PPR455825   [doi:10.1101/2022.02.17.480955, epmid:PPR455825]  None   
9    epmid:33713788    [doi:10.1016/j.jsb.2021.107716, epmid:33713788]  None   
10   epmid:30688648          [doi:10.7554/elife.43146, epmid:30688648]  None   
11   epmid:37040766    [doi:10.1016/j.str.2023.03.011, epmid:37040766]  None   
12  epmid:PPR509330   [doi:10.1101/2022.06.21.496981, epmid:PPR509330]  None   
13  epmid:PPR165454   [doi:10.1101/2020.05.19.104828, epmid:PPR165454]  None   
14  epmid:PPR432463   [doi:10.1101/2021.12.13.472487, epmid:PPR432463]  None   
15   epmid:36311290  [doi:10.1016/j.yjsbx.2022.100076, epmid:36311290]  None   
16   epmid:33298442       [doi:10.1126/sciadv.abc8258, epmid:33298442]  None   
17   epmid:36305590          [doi:10.7554/elife.82891, epmid:36305590]  None   
18   epmid:35982043   [doi:10.1038/s41467-022-32584-7, epmid:35982043]  None   
19  epmid:PPR448786   [doi:10.1101/2022.01.31.478342, epmid:PPR448786]  None   
20   epmid:33028835   [doi:10.1038/s41467-020-18803-z, epmid:33028835]  None   
21  epmid:PPR640429   [doi:10.1101/2022.06.13.496000, epmid:PPR640429]  None   
22   epmid:37533259    [doi:10.1016/j.bpj.2023.07.030, epmid:37533259]  None   
23  epmid:PPR365661   [doi:10.1101/2021.07.06.451241, epmid:PPR365661]  None   
24   epmid:35487464    [doi:10.1016/j.jsb.2022.107860, epmid:35487464]  None   
25   epmid:35017666   [doi:10.1038/s42003-021-02962-w, epmid:35017666]  None   
26  epmid:PPR416040   [doi:10.1101/2021.11.02.466666, epmid:PPR416040]  None   
27   epmid:32270040       [doi:10.1126/sciadv.aay9572, epmid:32270040]  None   
28   epmid:32241888      [doi:10.1073/pnas.1916935117, epmid:32241888]  None   
29   epmid:33950014    [doi:10.1107/s2059798321002369, epmid:33950014]  None   
30  epmid:PPR446190   [doi:10.1101/2022.01.24.477598, epmid:PPR446190]  None   
31   epmid:24813625           [doi:10.1038/nmeth.2961, epmid:24813625]  None   
32   epmid:PPR94275               [doi:10.1101/786715, epmid:PPR94275]  None   
33   epmid:35301732     [doi:10.15252/embj.2021109523, epmid:35301732]  None   
34  epmid:PPR162323   [doi:10.1101/2020.05.13.094771, epmid:PPR162323]  None   
35  epmid:PPR215334   [doi:10.1101/2020.09.18.298562, epmid:PPR215334]  None   
36  epmid:PPR151569   [doi:10.1101/2020.04.16.045534, epmid:PPR151569]  None   
37  epmid:PPR539804   [doi:10.1101/2022.09.02.506334, epmid:PPR539804]  None   
38   epmid:33199282          [doi:10.1128/jb.00371-20, epmid:33199282]  None   
39   epmid:19278660    [doi:10.1016/j.str.2009.01.009, epmid:19278660]  None   
40   epmid:33368000  [doi:10.1007/978-1-0716-0966-8_4, epmid:33368000]  None   
41   epmid:30193460     [doi:10.1021/acs.jpcb.8b06822, epmid:30193460]  None   
42   epmid:26965631      [doi:10.1126/science.aad2001, epmid:26965631]  None   
43  epmid:PPR288649   [doi:10.1101/2021.02.24.432779, epmid:PPR288649]  None   
44   epmid:33891903    [doi:10.1016/j.jmb.2021.167004, epmid:33891903]  None   
45   epmid:34468314          [doi:10.7554/elife.73099, epmid:34468314]  None   
46   epmid:35862756          [doi:10.1128/jb.00144-22, epmid:35862756]  None   
47   epmid:32980553  [doi:10.1016/j.pdpdt.2020.102029, epmid:32980553]  None   
48   epmid:33154161      [doi:10.1073/pnas.1920323117, epmid:33154161]  None   
49   epmid:346431

In [3]:

q = db.session.query(ScientificKnowledgeExpression) \
                .filter(ScientificKnowledgeExpression.id == ScientificKnowledgeExpressionHasRepresentation.ScientificKnowledgeExpression_id) \
                .filter(ScientificKnowledgeExpressionHasRepresentation.has_representation_id == ScientificKnowledgeItem.id) \
                .filter(ScientificKnowledgeExpressionHasRepresentation.has_representation_id == ScientificKnowledgeItem.id) \
                .filter(ScientificKnowledgeItem.type == 'FullTextPaper')
l = []
for e in q.all():
    l.append({'id':e.id, 
              'citation':e.content, 
              'items':'|'.join([i.type for i in e.has_representation])})
df = pd.DataFrame(l)
df

NameError: name 'db' is not defined

In [24]:
print(i.type)

AttributeError: 'list' object has no attribute 'type'

In [25]:
q = db.session.query(ScientificKnowledgeExpression, ScientificKnowledgeItem, ScientificKnowledgeFragment) \
                .filter(ScientificKnowledgeExpression.id == ScientificKnowledgeExpressionHasRepresentation.ScientificKnowledgeExpression_id) \
                .filter(ScientificKnowledgeExpressionHasRepresentation.has_representation_id == ScientificKnowledgeItem.id) \
                .filter(ScientificKnowledgeItem.id == ScientificKnowledgeItemHasPart.ScientificKnowledgeItem_id) \
                .filter(ScientificKnowledgeItemHasPart.has_part_id == ScientificKnowledgeFragment.id) \
                .filter(ScientificKnowledgeItem.type == 'FullTextPaper') \
                .filter(ScientificKnowledgeExpression.id.like('%36690741%')) 
                
l = []
for e,i,f in q.all():
    #print(f)
    l.append({'expression':e.id, 
              'citation':e.content,
              'fragment_type': f.type,  
              'offset': f.offset,  
              'length': f.length,  
              'section_name': f.name,  
              'fragment_text': f.content })
df = pd.DataFrame(l)
df

expression                                           citation  \
0   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
1   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
2   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
3   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
4   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
5   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
6   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
7   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
8   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
9   epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
10  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
11  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
12  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
13  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
14  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
15  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
16  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
17  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
18  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
19  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
20  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
21  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
22  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
23  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
24  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
25  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
26  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
27  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
28  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
29  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
30  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
31  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
32  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
33  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
34  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
35  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
36  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
37  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
38  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
39  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
40  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   
41  epmid:36690741  de Teresa-Trueba I, Goetz SK, Mattausch A, Sto...   

   fragment_type  offset  length  \
0        section     173    1478   
1        section    5300    3656   
2        section   28977    1249   
3        section   30231    4509   
4        section   34746    2701   
5        section   37452    1984   
6        section   39440    3224   
7        section   42672    4969   
8        section   47648       7   
9        section   47657     621   
10       section   48282     741   
11       section   49027    1064   
12       section    8962       7   
13       section   50095    1223   
14       section   51322     517   
15       section   51843    1048   
16       section   52896    1792   
17       section   54693     480   
18       section   55177     366   
19       section   55547     532   
20       section   56083     666   
21       section   56753    1710   
22       section   58468    2343   
23  

In [9]:
df.id.to_list()

['epmid:36690741',
 'epmid:37176000',
 'epmid:37485371',
 'epmid:33771860',
 'epmid:35508170',
 'epmid:30688648',
 'epmid:37040766',
 'epmid:36311290',
 'epmid:33298442',
 'epmid:36305590',
 'epmid:35982043',
 'epmid:33028835',
 'epmid:35017666',
 'epmid:32270040',
 'epmid:32241888',
 'epmid:33950014',
 'epmid:24813625',
 'epmid:33199282',
 'epmid:34468314',
 'epmid:35862756',
 'epmid:33154161',
 'epmid:34643180',
 'epmid:32341341',
 'epmid:33199285',
 'epmid:32849513']

In [10]:
from alhazen.tools.metadata_extraction_tool import MetadataExtractionTool
from alhazen.utils.local_literature_db import LocalLiteratureDb


db = LocalLiteratureDb('/Users/gburns/alhazen/', 'em_tech' )
met = MetadataExtractionTool(db, 'cryoet')

In [27]:
met.run('36690741', 'method')

[chain/start] [1:chain:RunnableSequence] Entering Chain run with input:
{
  "section_text": "Yeast cell culture\nS. pombe K972 Sp h- wild-type haploid cells were recovered from frozen stock by streaking on YES agar plates (YES Broth, Formedium, 20 g agarose per liter) and incubated at 30 degreesC for 1-3 days. Colonies were restreaked on fresh YES agar plates and incubated 1-3 days at 30 degreesC. Single colonies were inoculated in 5 ml YES medium (YES Broth, Formedium, PCM0302, FM0618/8573) and grown at 30 degreesC, 170 r.p.m. overnight (NCU-Shaker mini, Benchmark). On the next day, cultures were grown to their log phase at an optical density at 600 nm of 0.5-0.6 and diluted beforehand in YES if necessary.",
  "methodology": "Cryo-Electron Tomography (CryoET)",
  "method_goal": "to study the microscopic structure of a biological sample",
  "all_protocol_steps": "(A) the preparation of a biological sample for imaging (such as cells, tissue, a virus, a microorganism, etc.), (B) vitrific

In [25]:
print(completed_list)

['epmid:36690741', 'epmid:37176000', 'epmid:37485371', 'epmid:33771860', 'epmid:35508170', 'epmid:30688648', 'epmid:37040766', 'epmid:33298442', 'epmid:36305590', 'epmid:35982043', 'epmid:33028835', 'epmid:35017666', 'epmid:32270040', 'epmid:32241888', 'epmid:24813625', 'epmid:33199282', 'epmid:34468314', 'epmid:35862756', 'epmid:33154161', 'epmid:34643180']


In [27]:
from tqdm import tqdm
for id in tqdm(df.id.to_list()):
    if id in completed_list: 
        continue
    print(id)
    met.run(id, 'method')
    db.session.commit()

  0%|          | 0/25 [00:00<?, ?it/s]

epmid:36311290
epmid:33950014
epmid:32341341
[chain/start] [1:chain:RunnableSequence] Entering Chain run with input:
{
  "section_text": "Strains and growth conditions\nThe list of Vibrio cholerae strains and construction contains the wild-type: Vibrio cholerae C6706, the strain PM6: Deltavca1088, the strain PM7: Deltavca1093, Deltavca1094, Deltavca1095 (DeltaF7), and the strain PM18: Deltavca1092. V. cholerae deletion strains were generated using standard allele exchange34 with the following plasmids.\nPlasmid for deletion of vca1093, vca1094 and vca1095 (pPM045) was constructed by PCR amplification of the up- and down-stream regions of vca1093 and vca1095, respectively. PCR1 was performed with primers CCCCCTCTAGAAATTGGCTAATCCCTCCTAAACTC/AATCTTGCGCAGTTGTTCCATATC and C6706 chromosomal DNA as template. PCR2 was performed with primers GATATGGAACAACTGCGCAAGATT CGCTTAAGCACCACTGCCGAA/CCCCCTCTAGACATCATCAAATTCGTCGTCATGC and C6706 chromosomal DNA as template. A third PCR was then performed usi

 92%|█████████▏| 23/25 [18:56<01:38, 49.42s/it]

[llm/end] [1:chain:RunnableSequence > 3:llm:Ollama] [19.76s] Exiting LLM run with output:
{
  "generations": [
    [
      {
        "text": " {\"protocol_step\": G}\n\nThe text does not describe any of the specific steps of the protocol listed (A-F), but rather mentions a Nature Research Reporting Summary that provides further information on the research design. Therefore, the appropriate response is \"G) other protocol steps, not listed above.\"",
        "generation_info": {
          "model": "llama2:70b",
          "created_at": "2023-11-20T07:41:29.421935Z",
          "response": "",
          "done": true,
          "context": [
            29961,
            25580,
            29962,
            529,
            29879,
            24566,
            25580,
            29962,
            13,
            18884,
            3532,
            14816,
            29903,
            6778,
            3492,
            526,
            385,
            17924,
            4768,
        

 96%|█████████▌| 24/25 [28:38<01:20, 80.56s/it]

[llm/end] [1:chain:RunnableSequence > 3:llm:Ollama] [29.49s] Exiting LLM run with output:
{
  "generations": [
    [
      {
        "text": " {\n\"protocol_step\": \"G\"\n}\n\nThe text described the procedures followed as part of the protocol, specifically the step of milling the sample using a focussed ion beam (FIB) to create a thin, electron-transparent lamella. This step is not listed among the options A-F, so the corresponding value for the 'protocol_step' field is \"G\" for \"other protocol steps, not listed above\".",
        "generation_info": {
          "model": "llama2:70b",
          "created_at": "2023-11-20T07:51:11.3315Z",
          "response": "",
          "done": true,
          "context": [
            29961,
            25580,
            29962,
            529,
            29879,
            24566,
            25580,
            29962,
            13,
            18884,
            3532,
            14816,
            29903,
            6778,
            3492,
   

100%|██████████| 25/25 [48:27<00:00, 116.28s/it]

[llm/end] [1:chain:RunnableSequence > 3:llm:Ollama] [22.33s] Exiting LLM run with output:
{
  "generations": [
    [
      {
        "text": " {\n\"metadata_name\": \"reconstruction_method\",\n\"metadata_value\": \"Cryo-Electron Tomography (CryoET)\",\n\"original_text\": \"The C1-IgM model was built in the deposited cryo-ET 3D reconstruction (EMDB-4878) (17) using Pymol version 2.3.0.\"\n}",
        "generation_info": {
          "model": "llama2:70b",
          "created_at": "2023-11-20T08:10:59.832541Z",
          "response": "",
          "done": true,
          "context": [
            29961,
            25580,
            29962,
            529,
            29879,
            24566,
            25580,
            29962,
            13,
            18884,
            3532,
            14816,
            29903,
            6778,
            3492,
            526,
            385,
            17924,
            4768,
            5996,
            9638,
            391,
            29

In [1]:
import json
from alhazen.schema_sqla import ScientificKnowledgeFragmentHasNotes, Note

q1 = db.session.query(ScientificKnowledgeExpression) \
            .filter(ScientificKnowledgeExpression.id == ScientificKnowledgeExpressionHasRepresentation.ScientificKnowledgeExpression_id) \
            .filter(ScientificKnowledgeExpressionHasRepresentation.has_representation_id == ScientificKnowledgeItem.id) \
            .filter(ScientificKnowledgeItem.id == ScientificKnowledgeItemHasPart.ScientificKnowledgeItem_id ) \
            .filter(ScientificKnowledgeItemHasPart.has_part_id == ScientificKnowledgeFragment.id ) \
            .filter(ScientificKnowledgeFragment.id == ScientificKnowledgeFragmentHasNotes.ScientificKnowledgeFragment_id) \
            .filter(ScientificKnowledgeFragmentHasNotes.has_notes_id == Note.id) \
            .filter(ScientificKnowledgeItem.type == 'FullTextPaper') 
completed_list = [e.id for e in q1.all()]
print(completed_list)

NameError: name 'db' is not defined

In [29]:
print(len(completed_list))

23


In [5]:
import json
q1 = db.session.query(ScientificKnowledgeItem) \
            .filter(ScientificKnowledgeExpression.id == ScientificKnowledgeExpressionHasRepresentation.ScientificKnowledgeExpression_id) \
            .filter(ScientificKnowledgeExpressionHasRepresentation.has_representation_id == ScientificKnowledgeItem.id) \
            .filter(ScientificKnowledgeItem.type == 'FullTextPaper') \
            .filter(ScientificKnowledgeExpression.id.like('%36690741%')) 
i = q1.first()
l = []  
for f in i.has_part:
    for n in f.has_notes:
        if 'cryoet' in n.name:
            d = json.loads(n.content)
            d['section'] = f.name
            d['offset'] = f.offset
            d['length'] = f.length
            l.append(d)
df = pd.DataFrame(l)
df


metadata_name  \
0             organism_name   
1               cell_strain   
2             organism_name   
3               cell_strain   
4        sample_preparation   
..                      ...   
93    reconstruction_method   
94  reconstruction_software   
95    reconstruction_method   
96  reconstruction_software   
97            tomogram_size   

                                       metadata_value  \
0         S. pombe K972 Sp h- wild-type haploid cells   
1         S. pombe K972 Sp h- wild-type haploid cells   
2         S. pombe K972 Sp h- wild-type haploid cells   
3         S. pombe K972 Sp h- wild-type haploid cells   
4   recovered from frozen stock by streaking on YE...   
..                                                ...   
93                  threefold cross-validation scheme   
94                                        not present   
95     non-standard threefold cross-validation scheme   
96                                        not present   
97                                        not present   

                                        original_text  \
0   S. pombe K972 Sp h- wild-type haploid cells we...   
1   S. pombe K972 Sp h- wild-type haploid cells we...   
2   S. pombe K972 Sp h- wild-type haploid cells we...   
3   S. pombe K972 Sp h- wild-type haploid cells we...   
4   S. pombe K972 Sp h- wild-type haploid cells we...   
..                                                ...   
93  For ribosome and FAS localization, and for mem...   
94                                                      
95  For ribosome and FAS localization, and for mem...   
96                                                      
97                                                      

                                              section  offset  length  
0                       Methods >> Yeast cell culture   47657     621  
1                       Methods >> Yeast cell culture   47657     621  
2                       Methods >> Yeast cell culture   47657     621  
3                       Methods >> Yeast cell culture   47657     621  
4                       Methods >> Yeast cell culture   47657     621  
..                                                ...     ...     ...  
93  Methods >> Cross validation and performance ev...   63957    1649  
94  Methods >> Cross validation and performance ev...   63957    1649  
95  Methods >> Cross validation and performance ev...   63957    1649  
96  Methods >> Cross validation and performance ev...   63957    1649  
97  Methods >> Cross validation and performance ev...   63957    1649  

[98 rows x 6 columns]

In [18]:
import json
q1 = db.session.query(ScientificKnowledgeExpression, ScientificKnowledgeItem) \
            .filter(ScientificKnowledgeExpression.id == ScientificKnowledgeExpressionHasRepresentation.ScientificKnowledgeExpression_id) \
            .filter(ScientificKnowledgeExpressionHasRepresentation.has_representation_id == ScientificKnowledgeItem.id) \
            .filter(ScientificKnowledgeItem.type == 'FullTextPaper')  
papers = {}
for e,i in q1.all():
    for f in i.has_part:
        for n in f.has_notes:
            if 'cryoet' in n.name:
                papers[e.id] = e.content
print(len(papers))
print(papers)

23
{'epmid:36690741': 'de Teresa-Trueba I, Goetz SK, Mattausch A, Stojanovska F, Zimmerli CE, Toro-Nahuelpan M, Cheng DWC, Tollervey F, Pape C, Beck M, Diz-Muñoz A, Kreshuk A, Mahamid J, Zaugg JB. (2023) Convolutional networks for supervised mining of molecular patterns within cellular context.', 'epmid:37176000': 'Kaplan M, Yao Q, Jensen GJ. (2023) Structure and Assembly of the <i>Proteus mirabilis</i> Flagellar Motor by Cryo-Electron Tomography.', 'epmid:37485371': 'Shepherd DC, Kaplan M, Vankadari N, Kim KW, Larson CL, Dutka P, Beare PA, Krzymowski E, Heinzen RA, Jensen GJ, Ghosal D. (2023) Morphological remodeling of <i>Coxiella burnetii</i> during its biphasic developmental cycle revealed by cryo-electron tomography.', 'epmid:33771860': 'Mageswaran SK, Yang WY, Chakrabarty Y, Oikonomou CM, Jensen GJ. (2021) A cryo-electron tomography workflow reveals protrusion-mediated shedding on injured plasma membrane. ', 'epmid:35508170': 'Nicolas WJ, Fäßler F, Dutka P, Schur FKM, Jensen G, M

In [28]:
from alhazen.tools.metadata_extraction_tool import MetadataExtractionTool

loc = '/Users/gburns/alhazen/em_tech/reports/'
f = 'gjensen_papers.xlsx'
os.makedirs(loc, exist_ok=True)
with pd.ExcelWriter(f'{loc}{f}') as excel_writer:
    met = MetadataExtractionTool(db, 'cryoet')
    for id in papers:
        print(id)
        try:
            id2 = re.sub('epmid:', '', id)
            first_author = re.compile('^(.*?)[ \,\(]').search(papers[id]).group(1)
            year = re.compile('\((.*?)\)').search(papers[id]).group(1)
            cite  = f'{first_author}_{year}_{id2}'
            df, df_pivot = met.tabulate_fragments(id)
            df_pivot.to_excel(excel_writer, sheet_name=cite)
        except Exception as ex:
            print(ex)
            continue

epmid:36690741
Index contains duplicate entries, cannot reshape
epmid:37176000
epmid:37485371
epmid:33771860
epmid:35508170
epmid:30688648
epmid:37040766
epmid:33298442
epmid:36305590
epmid:35982043
epmid:33028835
epmid:35017666
epmid:32270040
epmid:32241888
epmid:24813625
epmid:33199282
epmid:34468314
epmid:35862756
epmid:33154161
epmid:34643180
epmid:32341341
epmid:33199285
epmid:32849513


In [45]:
extractions_pivot = df.pivot(index='metadata_name', columns=['offset', 'section'], values='metadata_value').fillna('')
extractions_pivot

offset                                                                   47657  \
section                                          Methods >> Yeast cell culture   
metadata_name                                                                    
annotated_entities                                                               
annotated_software                                                               
annotation_methods                                                               
biological_sample_type                                            cell culture   
camera_manufacturer                                                              
camera_model                                                                     
cell_strain                        S. pombe K972 Sp h- wild-type haploid cells   
cryoet_acceleration_voltage                                                      
cryoet_pixel_spacing                                                             
microscope_name                                                                  
microscope_setup                                                                 
organism_name                      S. pombe K972 Sp h- wild-type haploid cells   
reconstruction_method                                                            
reconstruction_software                                                          
sample_preparation           recovered from frozen stock by streaking on YE...   
tilt_maximum                                                                     
tilt_minimum                                                                     
tomogram_size                                                                    
total_flux                                                                       

offset                                         48282  \
section                     Methods >> Vitrification   
metadata_name                                          
annotated_entities                                     
annotated_software                                     
annotation_methods                                     
biological_sample_type                   yeast cells   
camera_manufacturer                                    
camera_model                                           
cell_strain                              not present   
cryoet_acceleration_voltage                            
cryoet_pixel_spacing                                   
microscope_name                                        
microscope_setup                                       
organism_name                                          
reconstruction_method                                  
reconstruction_software                                
sample_preparation                                     
tilt_maximum                                           
tilt_minimum                                           
tomogram_size                                          
total_flux                                             

offset                                                           50095  \
section                                             Methods >> Cryo-ET   
metadata_name                                                            
annotated_entities                                                       
annotated_software                                                       
annotation_methods                                                       
biological_sample_type                                                   
camera_manufacturer                                              Gatan   
camera_model                 K2 Summit direct detection camera (Gatan)   
cell_strain                                                              
cryoet_acceleration_voltage                                not present   
cryoet_pixel_spacing                                            3.45 A   
microscope_name                                            Titan Krios   


In [30]:
for n in db.list_notes_for_fragments_in_paper('cryoet', '36690741'):
    print(n)

In [18]:
item_type = 'FullTextPaper'
paper_id = '36690741'
q1 = db.session.query(ScientificKnowledgeItem) \
            .filter(ScientificKnowledgeExpressionHasRepresentation.has_representation_id == ScientificKnowledgeItem.id) \
            .filter(ScientificKnowledgeExpressionHasRepresentation.ScientificKnowledgeExpression_id.like('%'+str(paper_id)+'%')) 

i = q1.all()
print(i)

[ScientificKnowledgeItem(representation_of=epmid:36690741,creation_date=None,content=Convolutional networks for supervised mining of molecular patterns within cellular context.
Cryo-electron tomograms capture a wealth of structural information on the molecular constituents of cells and tissues. We present DeePiCt (deep picker in context), an open-source deep-learning framework for supervised segmentation and macromolecular complex localization in cryo-electron tomography. To train and benchmark DeePiCt on experimental data, we comprehensively annotated 20 tomograms of Schizosaccharomyces pombe for ribosomes, fatty acid synthases, membranes, nuclear pore complexes, organelles, and cytosol. By comparing DeePiCt to state-of-the-art approaches on this dataset, we show its unique ability to identify low-abundance and low-density complexes. We use DeePiCt to study compositionally distinct subpopulations of cellular ribosomes, with emphasis on their contextual association with mitochondria an

In [4]:
from alhazen.schema_sqla import InformationContentEntity, ScientificKnowledgeFragment

#ScientificKnowledgeFragment.__mapper_args__ = {
#    'concrete': True,
#    'polymorphic_identity': 'ScientificKnowledgeFragment', 
#    'polymorphic_load': 'inline'}
#ScientificKnowledgeFragment.__mapper__.polymorphic_load = 'inline'
#ScientificKnowledgeFragment.__mapper__.polymorphic_identity = 'ScientificKnowledgeFragment'
#ScientificKnowledgeFragment.__mapper__.concrete = True
ScientificKnowledgeFragment.__mapper__.polymorphic_load

In [ ]:
import urllib

os.environ['NCBI_API_KEY'] = 'd086451c882fabace54d7b049b6fb8481908'

def get_id(ice, t):
    idmap = {k[:k.find(':')]:k[k.find(':')+1:] for k in ice.xref} 
    return idmap.get(t)

path = '/users/gburns/alhazen/em_tech/nxml_files/'
dois = set()
for ske in db.session.query(ScientificKnowledgeExpression).all():
    doi = get_id(ske, 'doi')
    if doi is None or doi in dois:
        continue
    dois.add(doi)
    if os.path.exists(path+doi+'.nxml'):
        print('Skipping %s, already exists'%(doi))
        continue
    print('~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~')
    print('ID: %s'%(ske.id))  
    print('DOI: %s'%(doi))  
    print(ske.content)
    try:   
        get_nxml_from_pubmed_doi(doi, path)
        dois.add(doi)
    except URLError as ue:
        dois.remove(doi)
    except HTTPError as he:
        dois.remove(p.doi)


In [ ]:

pdf_path = '/Users/gburns/alhazen/em_tech/pdf_files/'
nxml_path = '/Users/gburns/alhazen/em_tech/nxml_files/'

l = []
for p in db.session.query(ScientificKnowledgeExpression).all():

    has_full_text = False
    has_full_text_methods = False
    has_pdf = False

    doi = doi = get_id(p, 'doi')
    if doi is None:
        continue
    
    pdf_file_path = pdf_path+doi+'.pdf'
    if os.path.exists(pdf_file_path):
        has_pdf = True

    nxml_file_path = nxml_path+doi+'.nxml'
    if os.path.exists(nxml_file_path):
        with open(nxml_file_path, 'r') as f:
            xml = f.read()
            soup = BeautifulSoup(xml, "lxml")
        body = soup.find_all('body')
        if body:
            has_full_text = True
        d = NxmlDoc(doi, xml)
        m = '\n'.join([d.read_section_text(sec) for sec in d.search_section_titles('methods')])
        if(len(m) > 0):
            has_full_text_methods = True

    l.append({'id':p.id, 'reference':p.content, 'doi':doi, 'pub_date':p.publication_date, 'has_full_text':has_full_text, 'has_full_text_methods':has_full_text_methods, 'has_pdf':has_pdf})

df = pd.DataFrame(l)
df        

In [6]:
from alhazen.schema_sqla import ScientificKnowledgeCollection, \
    ScientificKnowledgeExpression, ScientificKnowledgeCollectionHasMembers, \
    ScientificKnowledgeItem, ScientificKnowledgeExpressionHasRepresentation, \
    ScientificKnowledgeFragment, ScientificKnowledgeItemHasPart, \
    InformationResource

q = db.session.query(ScientificKnowledgeExpression) \
                .filter(ScientificKnowledgeExpression.id == ScientificKnowledgeExpressionHasRepresentation.ScientificKnowledgeExpression_id) \
                .filter(ScientificKnowledgeExpressionHasRepresentation.has_representation_id == ScientificKnowledgeItem.id) \
                .filter(ScientificKnowledgeExpressionHasRepresentation.has_representation_id == ScientificKnowledgeItem.id)

l = []
for e in q.all():
    l.append({'citation':e.content, 
              'items':'|'.join([i.type for i in e.has_representation])})
df = pd.DataFrame(l)
df

citation  \
0      (2023) Streamlined structure determination by...   
1      (2023) Visualizing the membrane disruption ac...   
2      (2023) Preparing <i>Arabidopsis thaliana</i> ...   
3      (2023) Cryo-electron tomography to study vira...   
4      (2023) <i>In situ</i>cryo-electron tomography...   
...                                                 ...   
2453   (2019) Orthobunyavirus spike architecture and...   
2454   (2014) Membrane deformation and scission by t...   
2455   (2016) A live RSV vaccine with engineered the...   
2456   (2015) Electron Tomography: A Three-Dimension...   
2457   (1966) [Retinopexis: comparative anatomical-p...   

                             items  
0     CitationRecord|FullTextPaper  
1     CitationRecord|FullTextPaper  
2     CitationRecord|FullTextPaper  
3     CitationRecord|FullTextPaper  
4                   CitationRecord  
...                            ...  
2453                CitationRecord  
2454                CitationRecord  
2455                CitationRecord  
2456                CitationRecord  
2457                CitationRecord  

[2458 rows x 2 columns]

In [ ]:
df[df.has_full_text_methods]

In [ ]:
print( df[df.has_pdf==True].shape ) 
print( df[df.has_full_text==True].shape ) 
print( df[df.has_full_text_methods==True].shape ) 
print( df.shape ) 


In [ ]:
years = [row.pub_date.year for i, row in df.iterrows() if row.pub_date.year>2000]

# draw histogram of publication years
import matplotlib.pyplot as plt
import numpy as np
plt.hist(years, bins=np.arange(min(years), max(years) + 1, 1))


In [ ]:
year1 = [row.pub_date.year for i, row in df.iterrows() if row.pub_date.year>2000 and (row.has_full_text | row.has_pdf)]
year2 = [row.pub_date.year for i, row in df.iterrows() if row.pub_date.year>2000]


# draw histogram of publication years
import matplotlib.pyplot as plt
import numpy as np
plt.hist(years, bins=np.arange(min(years), max(years) + 1, 1))


years = [row.pub_date.year for i, row in df.iterrows() if row.pub_date.year>2000 and row.has_full_text==True]

# draw histogram of publication years
import matplotlib.pyplot as plt
import numpy as np
plt.hist(years, bins=np.arange(min(years), max(years) + 1, 1))


In [ ]:

db = LocalLiteratureDb('em_literature', 'EuropePMC papers based on EM keywords', '/tmp/alhazen/')
if db.session is None:
    session_class = sessionmaker(bind=db.engine)
    db.session = session_class()

print([c.name for c in db.list_corpora()])

path = '/tmp/alhazen/nxml_files/'
methods = []
for i, p in enumerate(db.list_corpus_publications('1')):
    nxml_path = path+p.doi+'.nxml'
    if os.path.exists(nxml_path):
        with open(nxml_path, 'r') as f:
            xml = f.read()
            d = NxmlDoc(p.doi, xml)
            #print(p.doi)
            #print('~~~~~~~~~~~~~~~~~~~~~~~~~~~~')
            #for sec in d.search_section_titles('methods'):
            #    print(d.read_section_text(sec)) 
            #print('~~~~~~~~~~~~~~~~~~~~~~~~~~~~')
            m = '\n'.join([d.read_section_text(sec) for sec in d.search_section_titles('methods')])
            if(len(m) > 0):
                methods.append(m)

lengths = [(len(m) - len(re.sub('\s+','',m))) for m in methods]
lengths

In [ ]:
len(lengths)


In [ ]:
import base64
from IPython.display import Image, display
import matplotlib.pyplot as plt

def mm(graph):
  graphbytes = graph.encode("ascii")
  base64_bytes = base64.b64encode(graphbytes)
  base64_string = base64_bytes.decode("ascii")
  display(
    Image(
      url="https://mermaid.ink/img/"
      + base64_string
    )
  )



In [ ]:
engine = create_engine("sqlite:////tmp/alhazen/sciknow.db")
session_class = sessionmaker(bind=engine)
session = session_class()
p = linkml_sqla.ScientificPrimaryResearchPreprint(id=100, title='Test', abstract='Test abstract', iri='10.1234/1234', doi='10.1234/1234', publication_date=datetime.now())
session.add(p)
session.commit()

In [ ]:
!rm /tmp/alhazen/tmp.db

In [ ]:
!sqlite3 /tmp/alhazen/tmp.db "SELECT * FROM Work;" ".exit"

In [ ]:
for w in session.query(Work).where(Work.id!=100):
    print(p.title)
